In [2]:
import numpy as np

%matplotlib inline
import matplotlib.pyplot as plt

%load_ext autoreload
%autoreload 2

import sys
sys.path.append('../')
import scripts.load_dataset as load_dataset
import scripts.map_and_average as mapper
import scripts.classification
import scripts.outliers as outliers

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [4]:
OUTPUT_FILES = load_dataset.OUTPUT_FILES
n_iters = 10

In [ ]:
df = load_dataset.sample_dataset(csv_file=load_dataset.METADATA_FILE)
for n in range(n_iters):
    print "iteration %d" % n
    load_dataset.OUTPUT_FILES = [output_file.split('.pickle')[0]+'_'+str(n)+'.pickle' for 
                                 output_file in OUTPUT_FILES]
    load_dataset.features_for_train_test_sets(df, write_output=True)

In [ ]:
for n in range(n_iters):
    print "iteration %d" % n
    
    print "mapping..."
    mapper.INPUT_FILES = [output_file.split('.pickle')[0]+'_'+str(n)+'.pickle' for 
                                 output_file in OUTPUT_FILES]
    _, _, ldadata_list, _, _, Y, Yaudio = mapper.lda_map_and_average_frames(min_variance=0.99)
    X = np.concatenate(ldadata_list)
    
    # classification and confusion
    print "classifying..."
    traininds, testinds = classification.get_train_test_indices()
    X_train, Y_train, X_test, Y_test = classification.get_train_test_sets(X, Y, traininds, testinds)
    accuracy, _ = classification.confusion_matrix(X_train, Y_train, X_test, Y_test, saveCF=False, plots=False)
    print accuracy
    
    # outliers
    print "detecting outliers..."
    ddf = outliers.load_metadata(Yaudio, metadata_file=load_dataset.METADATA_FILE)
    df_global, threshold, MD = get_outliers_df(X, Y, chi2thr=0.999)
    print_most_least_outliers_topN(df_global, N=10)
    
    # write output
    print "writing file"
    df_global.to_csv('../data/outliers_'+str(n)+'.csv', index=False)